In [6]:
from pyspark.sql import SparkSession, functions as F
import pandas as pd 
from matplotlib import pyplot as plt 
import seaborn as sns 
from plotly import express as px

In [2]:
spark = SparkSession.builder.master("local[1]") \
                    .appName('SparkByExamples.com') \
                    .getOrCreate()

22/11/13 22:33:53 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
Using Spark's default log4j profile: org/apache/spark/log4j-defaults.properties
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).


In [9]:
df = pd.read_excel('Data/Data Model - Pizza Sales.xlsx')

In [14]:
df.to_csv('Data/PizzaSale.csv')

In [17]:
df = spark.read.csv('Data/PizzaSale.csv', header=True)

In [18]:
df.show()

+---+----------------+--------+--------------+--------+----------+----------+----------+-----------+----------+--------------+--------------------+--------------------+
|_c0|order_details_id|order_id|      pizza_id|quantity|order_date|order_time|unit_price|total_price|pizza_size|pizza_category|   pizza_ingredients|          pizza_name|
+---+----------------+--------+--------------+--------+----------+----------+----------+-----------+----------+--------------+--------------------+--------------------+
|  0|               1|       1|    hawaiian_m|       1|2015-01-01|  11:38:36|     13.25|      13.25|         M|       Classic|Sliced Ham, Pinea...|  The Hawaiian Pizza|
|  1|               2|       2| classic_dlx_m|       1|2015-01-01|  11:57:40|      16.0|       16.0|         M|       Classic|Pepperoni, Mushro...|The Classic Delux...|
|  2|               3|       2| five_cheese_l|       1|2015-01-01|  11:57:40|      18.5|       18.5|         L|        Veggie|Mozzarella Cheese...|The Five

22/11/13 22:40:35 WARN CSVHeaderChecker: CSV header does not conform to the schema.
 Header: , order_details_id, order_id, pizza_id, quantity, order_date, order_time, unit_price, total_price, pizza_size, pizza_category, pizza_ingredients, pizza_name
 Schema: _c0, order_details_id, order_id, pizza_id, quantity, order_date, order_time, unit_price, total_price, pizza_size, pizza_category, pizza_ingredients, pizza_name
Expected: _c0 but found: 
CSV file: file:///media/dmk/D:/Data/Project/DataScience/EDATutorial/Data/PizzaSale.csv


# About dataset 
## Contents 
- order_id: Unique identifier for each pizza placed by a table 
- pizza_id: Unique key identifier that ties the pizza orderd to its details, like size and price 
- total_price: unit_price * quantity 


In [28]:
df.summary().show()

22/11/13 22:45:41 WARN CSVHeaderChecker: CSV header does not conform to the schema.
 Header: , order_details_id, order_id, pizza_id, quantity, order_date, order_time, unit_price, total_price, pizza_size, pizza_category, pizza_ingredients, pizza_name
 Schema: _c0, order_details_id, order_id, pizza_id, quantity, order_date, order_time, unit_price, total_price, pizza_size, pizza_category, pizza_ingredients, pizza_name
Expected: _c0 but found: 
CSV file: file:///media/dmk/D:/Data/Project/DataScience/EDATutorial/Data/PizzaSale.csv


+-------+------------------+------------------+------------------+------------+------------------+----------+----------+------------------+-----------------+----------+--------------+---------------------+--------------------+
|summary|               _c0|  order_details_id|          order_id|    pizza_id|          quantity|order_date|order_time|        unit_price|      total_price|pizza_size|pizza_category|    pizza_ingredients|          pizza_name|
+-------+------------------+------------------+------------------+------------+------------------+----------+----------+------------------+-----------------+----------+--------------+---------------------+--------------------+
|  count|             48620|             48620|             48620|       48620|             48620|     48620|     48620|             48620|            48620|     48620|         48620|                48620|               48620|
|   mean|           24309.5|           24310.5|10701.479761415056|        null|1.01962155491

In [21]:
df.columns

['_c0',
 'order_details_id',
 'order_id',
 'pizza_id',
 'quantity',
 'order_date',
 'order_time',
 'unit_price',
 'total_price',
 'pizza_size',
 'pizza_category',
 'pizza_ingredients',
 'pizza_name']

In [24]:
df.select([F.count(F.when(F.isnan(c) | F.col(c).isNull(), c)).alias(c) for c in df.columns]).show()

22/11/13 22:43:24 WARN CSVHeaderChecker: CSV header does not conform to the schema.
 Header: , order_details_id, order_id, pizza_id, quantity, order_date, order_time, unit_price, total_price, pizza_size, pizza_category, pizza_ingredients, pizza_name
 Schema: _c0, order_details_id, order_id, pizza_id, quantity, order_date, order_time, unit_price, total_price, pizza_size, pizza_category, pizza_ingredients, pizza_name
Expected: _c0 but found: 
CSV file: file:///media/dmk/D:/Data/Project/DataScience/EDATutorial/Data/PizzaSale.csv


+---+----------------+--------+--------+--------+----------+----------+----------+-----------+----------+--------------+-----------------+----------+
|_c0|order_details_id|order_id|pizza_id|quantity|order_date|order_time|unit_price|total_price|pizza_size|pizza_category|pizza_ingredients|pizza_name|
+---+----------------+--------+--------+--------+----------+----------+----------+-----------+----------+--------------+-----------------+----------+
|  0|               0|       0|       0|       0|         0|         0|         0|          0|         0|             0|                0|         0|
+---+----------------+--------+--------+--------+----------+----------+----------+-----------+----------+--------------+-----------------+----------+



In [58]:
split_cols = F.split(df['order_time'], ':')
df = df.withColumn('hour', split_cols.getItem(0).cast('int')) \
       .withColumn('minute', split_cols.getItem(1).cast('int')) \
       .withColumn('second', split_cols.getItem(2).cast('int'))

In [59]:
df = df.withColumn('order_day', F.date_format('order_date', 'EEEE'))

In [60]:
df = df.withColumn('order_month', F.split('order_date', '-')[1].cast('int'))

In [61]:
df.show(3, truncate=False)

+---+----------------+--------+-------------+--------+----------+----------+----------+-----------+----------+--------------+--------------------------------------------------------------------------------------------+------------------------+----+------+------+---------+-----------+
|_c0|order_details_id|order_id|pizza_id     |quantity|order_date|order_time|unit_price|total_price|pizza_size|pizza_category|pizza_ingredients                                                                           |pizza_name              |hour|minute|second|order_day|order_month|
+---+----------------+--------+-------------+--------+----------+----------+----------+-----------+----------+--------------+--------------------------------------------------------------------------------------------+------------------------+----+------+------+---------+-----------+
|0  |1               |1       |hawaiian_m   |1       |2015-01-01|11:38:36  |13.25     |13.25      |M         |Classic       |Sliced Ham, Pineappl

22/11/13 23:31:35 WARN CSVHeaderChecker: CSV header does not conform to the schema.
 Header: , order_details_id, order_id, pizza_id, quantity, order_date, order_time, unit_price, total_price, pizza_size, pizza_category, pizza_ingredients, pizza_name
 Schema: _c0, order_details_id, order_id, pizza_id, quantity, order_date, order_time, unit_price, total_price, pizza_size, pizza_category, pizza_ingredients, pizza_name
Expected: _c0 but found: 
CSV file: file:///media/dmk/D:/Data/Project/DataScience/EDATutorial/Data/PizzaSale.csv


In [72]:
df.groupBy('pizza_size').agg(F.round(F.sum('total_price'), 4).alias('total_price')).show()

+----------+-----------+
|pizza_size|total_price|
+----------+-----------+
|        XL|    14076.0|
|         M|  249382.25|
|         L|   375318.7|
|         S|   178076.5|
|       XXL|     1006.6|
+----------+-----------+



In [62]:
df_temp = df.toPandas()

22/11/13 23:31:36 WARN CSVHeaderChecker: CSV header does not conform to the schema.
 Header: , order_details_id, order_id, pizza_id, quantity, order_date, order_time, unit_price, total_price, pizza_size, pizza_category, pizza_ingredients, pizza_name
 Schema: _c0, order_details_id, order_id, pizza_id, quantity, order_date, order_time, unit_price, total_price, pizza_size, pizza_category, pizza_ingredients, pizza_name
Expected: _c0 but found: 
CSV file: file:///media/dmk/D:/Data/Project/DataScience/EDATutorial/Data/PizzaSale.csv


In [63]:
df_temp

_c0 order_details_id order_id       pizza_id quantity  order_date  \
0          0                1        1     hawaiian_m        1  2015-01-01   
1          1                2        2  classic_dlx_m        1  2015-01-01   
2          2                3        2  five_cheese_l        1  2015-01-01   
3          3                4        2    ital_supr_l        1  2015-01-01   
4          4                5        2     mexicana_m        1  2015-01-01   
...      ...              ...      ...            ...      ...         ...   
48615  48615            48616    21348  ckn_alfredo_m        1  2015-12-31   
48616  48616            48617    21348  four_cheese_l        1  2015-12-31   
48617  48617            48618    21348   napolitana_s        1  2015-12-31   
48618  48618            48619    21349     mexicana_l        1  2015-12-31   
48619  48619            48620    21350      bbq_ckn_s        1  2015-12-31   

      order_time unit_price total_price pizza_size pizza_category  \
0       11:38:36      13.25       13.25          M        Classic   
1       11:57:40       16.0        16.0          M        Classic   
2       11:57:40       18.5        18.5          L         Veggie   
3       11:57:40      20.75       20.75          L        Supreme   
4       11:57:40       16.0        16.0          M         Veggie   
...          ...        ...         ...        ...            ...   
48615   21:23:10      16.75       16.75          M        Chicken   
48616   21:23:10      17.95       17.95          L         Veggie   
48617   21:23:10       12.0        12.0          S        Classic   
48618   22:09:54      20.25       20.25          L         Veggie   
48619   23:02:05      12.75       12.75          S        Chicken   

                                       pizza_ingredients  \
0               Sliced Ham, Pineapple, Mozzarella Cheese   
1      Pepperoni, Mushrooms, Red Onions, Red Peppers,...   
2      Mozzarella Cheese, Provolone Cheese, Smoked Go...   
3      Calabrese Salami, Capocollo, Tomatoes, Red Oni...   
4      Tomatoes, Red Peppers, Jalapeno Peppers, Red O...   
...                                                  ...   
48615  Chicken, Red Onions, Red Peppers, Mushrooms, A...   
48616  Ricotta Cheese, Gorgonzola Piccante Cheese, Mo...   
48617  Tomatoes, Anchovies, Green Olives, Red Onions,...   
48618  Tomatoes, Red Peppers, Jalapeno Peppers, Red O...   
48619  Barbecued Chicken, Red Peppers, Green Peppers,...   

                       pizza_name  hour  minute  second order_day  order_month  
0              The Hawaiian Pizza    11      38      36  Thursday            1  
1        The Classic Deluxe Pizza    11      57      40  Thursday            1  
2           The Five Cheese Pizza    11      57      40  Thursday            1  
3       The Italian Supreme Pizza    11      57      40  Thursday            1  
4              The Mexicana Pizza    11      57      40  Thursday            1  
...                           ...   ...     ...     ...       ...          ...  
48615   The Chicken Alfredo Pizza    21      23      10  Thursday           12  
48616       The Four Cheese Pizza    21      23      10  Thursday           12  
48617        The Napolitana Pizza    21      23      10  Thursday           12  
48618          The Mexicana Pizza    22       9      54  Thursday           12  
48619  The Barbecue Chicken Pizza    23       2       5  Thursday           12  

[48620 rows x 18 columns]

# 1. Plot some feature

In [64]:
px.histogram(df_temp, x='pizza_size')

In [65]:
px.histogram(df_temp, x='pizza_category')

In [66]:
fig = px.histogram(df_temp, x='pizza_name', height=800)
fig.update_xaxes(tickangle=-45)

In [68]:
px.histogram(df_temmp, x='hour')